In [2]:
import pandas as pd
import numpy as np
import nltk
from nltk.tokenize import sent_tokenize, word_tokenize
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from nltk.tokenize import PunktSentenceTokenizer
from nltk.stem import SnowballStemmer, LancasterStemmer

In [3]:
df = pd.read_csv("coffee_fix.csv")
df.head()

slug  \
0  https://www.coffeereview.com/review/sweety-esp...   
1  https://www.coffeereview.com/review/flora-blen...   
2  https://www.coffeereview.com/review/ethiopia-s...   
3  https://www.coffeereview.com/review/ethiopia-s...   
4  https://www.coffeereview.com/review/ethiopia-g...   

                                            all_text  rating  \
0   \r\n\r\n\r\n95\r\n\r\n\r\nA.R.C.\r\n“Sweety” ...      95   
1   \r\n\r\n\r\n94\r\n\r\n\r\nA.R.C.\r\nFlora Ble...      94   
2   \r\n\r\n\r\n92\r\n\r\n\r\nRevel Coffee\r\nEth...      92   
3   \r\n\r\n\r\n92\r\n\r\n\r\nRoast House\r\nEthi...      92   
4   \r\n\r\n\r\n94\r\n\r\n\r\nBig Creek Coffee Ro...      94   

                     roaster                        name             location  \
0                     A.R.C.     “Sweety” Espresso Blend     Hong Kong, China   
1                     A.R.C.        Flora Blend Espresso     Hong Kong, China   
2               Revel Coffee    Ethiopia Shakiso Mormora    Billings, Montana   
3                Roast House          Ethiopia Suke Quto  Spokane, Washington   
4  Big Creek Coffee Roasters  Ethiopia Gedeb Halo Beriti    Hamilton, Montana   

                                             origin         roast  \
0                                  Panama; Ethiopia  Medium-Light   
1                              Africa; Asia Pacific  Medium-Light   
2                      Guji Zone, southern Ethiopia  Medium-Light   
3  Guji Zone, Oromia Region, south-central Ethiopia  Medium-Light   
4     Gedeb District, Gedeo Zone, southern Ethiopia        Medium   

            est_price    review_date agtron  aroma  acid  body  flavor  \
0  HKD $250/227 grams  November 2017  50/73    9.0   NaN   9.0     9.0   
1  HKD $158/227 grams  November 2017  54/77    9.0   NaN   9.0     9.0   
2    $16.00/12 ounces  November 2017  54/70    9.0   8.0   8.0     9.0   
3    $19.00/16 ounces  November 2017  53/79    8.0   8.0   9.0     9.0   
4    $16.50/12 ounces  November 2017  48/70    9.0   9.0   9.0     9.0   

   aftertaste  with_milk                                             desc_1  \
0         9.0        9.0  Evaluated as espresso. Sweet-toned, deeply ric...   
1         8.0        9.0  Evaluated as espresso. Sweetly tart, floral-to...   
2         8.0        NaN  Crisply sweet, cocoa-toned. Lemon blossom, roa...   
3         8.0        NaN  Delicate, sweetly spice-toned. Pink peppercorn...   
4         8.0        NaN  Deeply sweet, subtly pungent. Honey, pear, tan...   

                                              desc_2  \
0  An espresso blend comprised of coffees from Pa...   
1  An espresso blend comprised of coffees from Af...   
2  This coffee tied for the third-highest rating ...   
3  This coffee tied for the third-highest rating ...   
4  Southern Ethiopia coffees like this one are pr...   

                                              desc_3  
0  A radiant espresso blend that shines equally i...  
1  A floral-driven straight shot, amplified with ...  
2  A gently spice-toned, floral- driven wet-proce...  
3  Lavender-like flowers and hints of zesty pink ...  
4  A deeply and generously lush cup saved from se...

In [4]:
tokens = [word_tokenize(i) for i in df["desc_1"]]
t1 = tokens[0]

In [5]:
t1

['Evaluated',
 'as',
 'espresso',
 '.',
 'Sweet-toned',
 ',',
 'deeply',
 'rich',
 ',',
 'chocolaty',
 '.',
 'Vanilla',
 'paste',
 ',',
 'dark',
 'chocolate',
 ',',
 'narcissus',
 ',',
 'pink',
 'grapefruit',
 'zest',
 ',',
 'black',
 'cherry',
 'in',
 'aroma',
 'and',
 'cup',
 '.',
 'Plush',
 ',',
 'syrupy',
 'mouthfeel',
 ';',
 'resonant',
 ',',
 'flavor-saturated',
 'finish',
 '.',
 'In',
 'three',
 'parts',
 'milk',
 ',',
 'rich',
 'chocolate',
 'tones',
 'intensify',
 ',',
 'along',
 'with',
 'intimations',
 'of',
 'vanilla',
 'paste',
 'and',
 'black',
 'cherry',
 'in',
 'the',
 'short',
 'finish',
 'and',
 'floral-toned',
 'citrus',
 'zest',
 'in',
 'the',
 'long',
 '.']

In [6]:
count = 0
for i in df["desc_1"]:
    if "three parts milk" in i:
        #print(i)
        count += 1
print(count)

210


In [7]:
def process_content(description):
    l = []
    try:
        words = nltk.word_tokenize(description.lower().replace("-"," "))
        #print(words)
        tagged = nltk.pos_tag(words)
        #print(tagged)

        # All chunks
        chunk_gram = r"""Chunk: {<NNP>?<RB.?>*<VBD>*<JJ.?>*<NNP.?>*<NN.?>*<NN.?>*}"""
        chunk_parser = nltk.RegexpParser(chunk_gram)
        chunked = chunk_parser.parse(tagged)

        # Finding the finish description
        finish_gram = r"""Chunk: {<NNP>?<RB.?>*<VBD>*<VBN>*<JJ.?>*<NNP.?>*<NN.?>*<NN.?>*<IN>+<DT>+<JJ.?>*<NN>*}"""
        finish_parser = nltk.RegexpParser(finish_gram)
        finish_chunks = finish_parser.parse(tagged)

        # Finding the milk description
        
        # print(description)

        for chunk in chunked:
            if hasattr(chunk,"label"):
                if chunk.label() == "Chunk":
                    l.append(chunk)
            # print(chunk)
        #print("---Finish---")
        if len(finish_chunks) == 0:
            for chunk in chunked:
                if hasattr(chunk,"label"):
                    if chunk.label() == "Chunk":
                        for j in chunk:
                            print(j[0])
        # for chunk in finish_chunks:
        #     if hasattr(chunk,"label"):
        #         if chunk.label() == "Chunk":
        #             print(chunk)
        #             # for j in chunk:
        #             #     print(j[0])
        #print("---Finish done---")

    except Exception as e:
        print(str(e))

    return l

chunks = process_content(df["desc_1"][0])
chunks

[Tree('Chunk', [('espresso', 'NN')]),
 Tree('Chunk', [('sweet', 'NN')]),
 Tree('Chunk', [('toned', 'VBD')]),
 Tree('Chunk', [('deeply', 'RB'), ('rich', 'JJ')]),
 Tree('Chunk', [('chocolaty', 'NN')]),
 Tree('Chunk', [('vanilla', 'NN'), ('paste', 'NN')]),
 Tree('Chunk', [('dark', 'JJ'), ('chocolate', 'NN')]),
 Tree('Chunk', [('narcissus', 'NN')]),
 Tree('Chunk', [('grapefruit', 'NN'), ('zest', 'NN')]),
 Tree('Chunk', [('black', 'JJ'), ('cherry', 'NN')]),
 Tree('Chunk', [('aroma', 'NN')]),
 Tree('Chunk', [('cup', 'NN')]),
 Tree('Chunk', [('plush', 'NN')]),
 Tree('Chunk', [('syrupy', 'JJ'), ('mouthfeel', 'NN')]),
 Tree('Chunk', [('resonant', 'NN')]),
 Tree('Chunk', [('flavor', 'NN')]),
 Tree('Chunk', [('saturated', 'VBD'), ('finish', 'JJ')]),
 Tree('Chunk', [('parts', 'NNS'), ('milk', 'NN')]),
 Tree('Chunk', [('rich', 'JJ'), ('chocolate', 'NN'), ('tones', 'NNS')]),
 Tree('Chunk', [('intimations', 'NNS')]),
 Tree('Chunk', [('vanilla', 'NN'), ('paste', 'NN')]),
 Tree('Chunk', [('black', 'JJ'

In [8]:
useless = ["milk","short","long","cup","flavor",
    "flavour","www","http","visit","information"
    "cafe","coffee","coffees","blend","shot"]

characteristic_names = ["finish","tone","tones","toned","mouthfeel","paste"
    "note","notes"]

def clean_chunk(chunk):
    grammar = [i[1] for i in chunk]
    words = [i[0] for i in chunk]
    for i in characteristic_names:
        for j in chunk:
            if j[0] == i:
                chunk.remove(j)
    for i in useless:
        if i in "".join(words):
            return None
    return chunk

In [9]:
clean = [clean_chunk(i) for i in chunks if clean_chunk(i) is not None]
clean

[Tree('Chunk', [('espresso', 'NN')]),
 Tree('Chunk', [('sweet', 'NN')]),
 Tree('Chunk', []),
 Tree('Chunk', [('deeply', 'RB'), ('rich', 'JJ')]),
 Tree('Chunk', [('chocolaty', 'NN')]),
 Tree('Chunk', [('vanilla', 'NN'), ('paste', 'NN')]),
 Tree('Chunk', [('dark', 'JJ'), ('chocolate', 'NN')]),
 Tree('Chunk', [('narcissus', 'NN')]),
 Tree('Chunk', [('grapefruit', 'NN'), ('zest', 'NN')]),
 Tree('Chunk', [('black', 'JJ'), ('cherry', 'NN')]),
 Tree('Chunk', [('aroma', 'NN')]),
 Tree('Chunk', [('plush', 'NN')]),
 Tree('Chunk', [('syrupy', 'JJ')]),
 Tree('Chunk', [('resonant', 'NN')]),
 Tree('Chunk', [('saturated', 'VBD')]),
 Tree('Chunk', [('rich', 'JJ'), ('chocolate', 'NN')]),
 Tree('Chunk', [('intimations', 'NNS')]),
 Tree('Chunk', [('vanilla', 'NN'), ('paste', 'NN')]),
 Tree('Chunk', [('black', 'JJ'), ('cherry', 'NN')]),
 Tree('Chunk', [('floral', 'JJ')]),
 Tree('Chunk', [('citrus', 'NN'), ('zest', 'NN')])]

In [10]:
stemmer = PorterStemmer()
stemmer = SnowballStemmer(language = "english")

In [11]:
def extract_characteristics(raw):
    characteristics = []
    for chunk in raw:
        grammar = [i[1] for i in chunk]
        words = [i[0] for i in chunk]
        clean = clean_chunk(chunk)
        if clean is None:
            continue

        if len(clean) == 0:
            continue
        
        if len(clean) == 1:
            if grammar[0] != "VBD":
                characteristics.append(stemmer.stem(words[0]))
            continue

        if all(i=="NN" for i in grammar):
            characteristics.append(stemmer.stem(words[0]))
            continue
        
        elif grammar[0].startswith('JJ') and grammar[1].startswith('NN'):
            characteristics.append(stemmer.stem(words[1]))
            continue

        elif grammar[0].startswith('RB') and grammar[1].startswith('JJ'):
            characteristics.append(stemmer.stem(words[1]))
            continue
    return np.array(characteristics)

extract_characteristics(chunks)

array(['espresso', 'sweet', 'rich', 'chocolati', 'vanilla', 'chocol',
       'narcissus', 'grapefruit', 'cherri', 'aroma', 'plush', 'syrupi',
       'reson', 'chocol', 'intim', 'vanilla', 'cherri', 'floral',
       'citrus'], dtype='<U10')

In [12]:
df["characteristics"] = df["desc_1"].apply(lambda x:extract_characteristics(process_content(x)))

In [13]:
df.head()

slug  \
0  https://www.coffeereview.com/review/sweety-esp...   
1  https://www.coffeereview.com/review/flora-blen...   
2  https://www.coffeereview.com/review/ethiopia-s...   
3  https://www.coffeereview.com/review/ethiopia-s...   
4  https://www.coffeereview.com/review/ethiopia-g...   

                                            all_text  rating  \
0   \r\n\r\n\r\n95\r\n\r\n\r\nA.R.C.\r\n“Sweety” ...      95   
1   \r\n\r\n\r\n94\r\n\r\n\r\nA.R.C.\r\nFlora Ble...      94   
2   \r\n\r\n\r\n92\r\n\r\n\r\nRevel Coffee\r\nEth...      92   
3   \r\n\r\n\r\n92\r\n\r\n\r\nRoast House\r\nEthi...      92   
4   \r\n\r\n\r\n94\r\n\r\n\r\nBig Creek Coffee Ro...      94   

                     roaster                        name             location  \
0                     A.R.C.     “Sweety” Espresso Blend     Hong Kong, China   
1                     A.R.C.        Flora Blend Espresso     Hong Kong, China   
2               Revel Coffee    Ethiopia Shakiso Mormora    Billings, Montana   
3                Roast House          Ethiopia Suke Quto  Spokane, Washington   
4  Big Creek Coffee Roasters  Ethiopia Gedeb Halo Beriti    Hamilton, Montana   

                                             origin         roast  \
0                                  Panama; Ethiopia  Medium-Light   
1                              Africa; Asia Pacific  Medium-Light   
2                      Guji Zone, southern Ethiopia  Medium-Light   
3  Guji Zone, Oromia Region, south-central Ethiopia  Medium-Light   
4     Gedeb District, Gedeo Zone, southern Ethiopia        Medium   

            est_price    review_date  ... aroma  acid  body  flavor  \
0  HKD $250/227 grams  November 2017  ...   9.0   NaN   9.0     9.0   
1  HKD $158/227 grams  November 2017  ...   9.0   NaN   9.0     9.0   
2    $16.00/12 ounces  November 2017  ...   9.0   8.0   8.0     9.0   
3    $19.00/16 ounces  November 2017  ...   8.0   8.0   9.0     9.0   
4    $16.50/12 ounces  November 2017  ...   9.0   9.0   9.0     9.0   

   aftertaste  with_milk                                             desc_1  \
0         9.0        9.0  Evaluated as espresso. Sweet-toned, deeply ric...   
1         8.0        9.0  Evaluated as espresso. Sweetly tart, floral-to...   
2         8.0        NaN  Crisply sweet, cocoa-toned. Lemon blossom, roa...   
3         8.0        NaN  Delicate, sweetly spice-toned. Pink peppercorn...   
4         8.0        NaN  Deeply sweet, subtly pungent. Honey, pear, tan...   

                                              desc_2  \
0  An espresso blend comprised of coffees from Pa...   
1  An espresso blend comprised of coffees from Af...   
2  This coffee tied for the third-highest rating ...   
3  This coffee tied for the third-highest rating ...   
4  Southern Ethiopia coffees like this one are pr...   

                                              desc_3  \
0  A radiant espresso blend that shines equally i...   
1  A floral-driven straight shot, amplified with ...   
2  A gently spice-toned, floral- driven wet-proce...   
3  Lavender-like flowers and hints of zesty pink ...   
4  A deeply and generously lush cup saved from se...   

                                     characteristics  
0  [espresso, sweet, rich, chocolati, vanilla, ch...  
1  [espresso, floral, honeysuckl, oak, chocol, th...  
2  [crispli, cocoa, blossom, date, rice, pepperco...  
3  [delic, peppercorn, date, myrrh, lavend, aroma...  
4  [sweet, pungent, honey, pear, tangerin, zest, ...  

[5 rows x 21 columns]

In [14]:
all_characteristics = set([])
for i in df["characteristics"]:
    all_characteristics.update(i)

all_characteristics

{'access',
 'acid',
 'acrid',
 'addit',
 'adult',
 'agav',
 'akin',
 'alcohol',
 'aliv',
 'all',
 'allspic',
 'almond',
 'almondi',
 'almost',
 'aloewood',
 'also',
 'alyssum',
 'amber',
 'amond',
 'amplif',
 'amplifi',
 'anchor',
 'anis',
 'appeal',
 'appear',
 'appl',
 'apricot',
 'aprium',
 'aroma',
 'aromat',
 'array',
 'assess',
 'attract',
 'author',
 'autumn',
 'azalea',
 'back',
 'backdrop',
 'background',
 'bacon',
 'bake',
 'baker',
 'balanc',
 'ballast',
 'balm',
 'balsa',
 'banana',
 'barley',
 'barrel',
 'base',
 'bay',
 'bean',
 'beauti',
 'beef',
 'bergamot',
 'berri',
 'beverag',
 'big',
 'bight',
 'bing',
 'bit',
 'bitter',
 'bitter/tart',
 'bitterish',
 'bittersweet',
 'bizarr',
 'blackberri',
 'blackcurr',
 'blood',
 'bloom',
 'blossom',
 'blueberri',
 'bodi',
 'bold',
 'bosc',
 'bottom',
 'bouquet',
 'bourbon',
 'boysenberri',
 'brace',
 'brandi',
 'brazil',
 'breadfruit',
 'brew',
 'bright',
 'brilliant',
 'brisk',
 'brittl',
 'brothi',
 'brown',
 'bubblegum',
 'bu

In [15]:
df["coffee"] = df["name"] + "-" + df["roaster"]
df.head(3)

slug  \
0  https://www.coffeereview.com/review/sweety-esp...   
1  https://www.coffeereview.com/review/flora-blen...   
2  https://www.coffeereview.com/review/ethiopia-s...   

                                            all_text  rating       roaster  \
0   \r\n\r\n\r\n95\r\n\r\n\r\nA.R.C.\r\n“Sweety” ...      95        A.R.C.   
1   \r\n\r\n\r\n94\r\n\r\n\r\nA.R.C.\r\nFlora Ble...      94        A.R.C.   
2   \r\n\r\n\r\n92\r\n\r\n\r\nRevel Coffee\r\nEth...      92  Revel Coffee   

                       name           location                        origin  \
0   “Sweety” Espresso Blend   Hong Kong, China              Panama; Ethiopia   
1      Flora Blend Espresso   Hong Kong, China          Africa; Asia Pacific   
2  Ethiopia Shakiso Mormora  Billings, Montana  Guji Zone, southern Ethiopia   

          roast           est_price    review_date  ... acid  body  flavor  \
0  Medium-Light  HKD $250/227 grams  November 2017  ...  NaN   9.0     9.0   
1  Medium-Light  HKD $158/227 grams  November 2017  ...  NaN   9.0     9.0   
2  Medium-Light    $16.00/12 ounces  November 2017  ...  8.0   8.0     9.0   

   aftertaste  with_milk                                             desc_1  \
0         9.0        9.0  Evaluated as espresso. Sweet-toned, deeply ric...   
1         8.0        9.0  Evaluated as espresso. Sweetly tart, floral-to...   
2         8.0        NaN  Crisply sweet, cocoa-toned. Lemon blossom, roa...   

                                              desc_2  \
0  An espresso blend comprised of coffees from Pa...   
1  An espresso blend comprised of coffees from Af...   
2  This coffee tied for the third-highest rating ...   

                                              desc_3  \
0  A radiant espresso blend that shines equally i...   
1  A floral-driven straight shot, amplified with ...   
2  A gently spice-toned, floral- driven wet-proce...   

                                     characteristics  \
0  [espresso, sweet, rich, chocolati, vanilla, ch...   
1  [espresso, floral, honeysuckl, oak, chocol, th...   
2  [crispli, cocoa, blossom, date, rice, pepperco...   

                                  coffee  
0         “Sweety” Espresso Blend-A.R.C.  
1            Flora Blend Espresso-A.R.C.  
2  Ethiopia Shakiso Mormora-Revel Coffee  

[3 rows x 22 columns]

In [16]:
# We want to remove characteristics that appear in less that 10% of the coffees
d = {}
for i in df["characteristics"]:
    for j in i:
        if j in d:
            d[j] += 1
        else:
            d[j] = 1

count_dict = {i:j for i,j in d.items() if j > len(df)/10}
count_dict

{'espresso': 315,
 'sweet': 1195,
 'rich': 415,
 'chocolati': 398,
 'chocol': 1558,
 'narcissus': 256,
 'cherri': 238,
 'aroma': 2255,
 'plush': 309,
 'syrupi': 536,
 'reson': 279,
 'floral': 487,
 'oak': 235,
 'gentl': 373,
 'crispli': 244,
 'cocoa': 1070,
 'delic': 230,
 'finish': 511,
 'hint': 433,
 'crisp': 536,
 'acid': 1239,
 'zest': 334,
 'juici': 553,
 'structur': 691,
 'almond': 579,
 'sandalwood': 340,
 'fruit': 435,
 'high': 271,
 'apricot': 267,
 'magnolia': 291,
 'savori': 265,
 'full': 514,
 'cedar': 761,
 'cut': 317,
 'tart': 468,
 'hazelnut': 358,
 'satini': 354,
 'flower': 351,
 'underton': 256,
 'velveti': 293,
 'bright': 376}

In [17]:
one_hot = pd.DataFrame(columns = ["coffee"] + list(count_dict.keys()))
one_hot

Empty DataFrame
Columns: [coffee, espresso, sweet, rich, chocolati, chocol, narcissus, cherri, aroma, plush, syrupi, reson, floral, oak, gentl, crispli, cocoa, delic, finish, hint, crisp, acid, zest, juici, structur, almond, sandalwood, fruit, high, apricot, magnolia, savori, full, cedar, cut, tart, hazelnut, satini, flower, underton, velveti, bright]
Index: []

[0 rows x 42 columns]

In [18]:
d = {"coffee":df["coffee"]}

for i in count_dict.keys():
    d[i] = df["characteristics"].apply(lambda x: 0 if i in x else 1)

In [19]:
one_hot = pd.DataFrame(d)
one_hot.head()

coffee  espresso  sweet  rich  \
0                     “Sweety” Espresso Blend-A.R.C.         0      0     0   
1                        Flora Blend Espresso-A.R.C.         0      1     1   
2              Ethiopia Shakiso Mormora-Revel Coffee         1      1     0   
3                     Ethiopia Suke Quto-Roast House         1      1     1   
4  Ethiopia Gedeb Halo Beriti-Big Creek Coffee Ro...         1      0     1   

   chocolati  chocol  narcissus  cherri  aroma  plush  ...  full  cedar  cut  \
0          0       0          0       0      0      0  ...     1      1    1   
1          1       0          1       1      0      1  ...     1      1    1   
2          1       1          1       1      0      1  ...     1      1    1   
3          1       1          1       1      0      1  ...     1      1    1   
4          1       0          1       1      0      0  ...     1      1    1   

   tart  hazelnut  satini  flower  underton  velveti  bright  
0     1         1       1       1         1        1       1  
1     1         1       1       1         1        1       1  
2     1         1       1       1         1        1       1  
3     1         1       1       1         1        1       1  
4     1         1       1       1         1        1       1  

[5 rows x 42 columns]

In [20]:
from sklearn.neighbors import NearestNeighbors

In [21]:
one_hot[one_hot.columns[1:]]

espresso  sweet  rich  chocolati  chocol  narcissus  cherri  aroma  \
0            0      0     0          0       0          0       0      0   
1            0      1     1          1       0          1       1      0   
2            1      1     0          1       1          1       1      0   
3            1      1     1          1       1          1       1      0   
4            1      0     1          1       0          1       1      0   
...        ...    ...   ...        ...     ...        ...     ...    ...   
2277         1      1     1          1       0          1       1      0   
2278         1      1     1          0       1          1       1      0   
2279         1      0     1          1       1          0       0      0   
2280         1      0     1          0       0          1       1      0   
2281         0      1     1          1       0          1       1      0   

      plush  syrupi  ...  full  cedar  cut  tart  hazelnut  satini  flower  \
0         0       0  ...     1      1    1     1         1       1       1   
1         1       0  ...     1      1    1     1         1       1       1   
2         1       1  ...     1      1    1     1         1       1       1   
3         1       1  ...     1      1    1     1         1       1       1   
4         0       1  ...     1      1    1     1         1       1       1   
...     ...     ...  ...   ...    ...  ...   ...       ...     ...     ...   
2277      1       0  ...     1      1    1     1         1       1       1   
2278      1       1  ...     1      0    1     1         1       1       1   
2279      1       1  ...     1      1    1     1         1       1       1   
2280      1       0  ...     1      1    1     0         0       1       1   
2281      1       0  ...     1      0    1     1         0       1       1   

      underton  velveti  bright  
0            1        1       1  
1            1        1       1  
2            1        1       1  
3            1        1       1  
4            1        1       1  
...        ...      ...     ...  
2277         1        1       1  
2278         1        1       1  
2279         1        1       1  
2280         1        1       1  
2281         1        1       1  

[2282 rows x 41 columns]

In [22]:
X = one_hot[one_hot.columns[1:]]
nbrs = NearestNeighbors(n_neighbors=6, algorithm='ball_tree').fit(X)
distances, indices = nbrs.kneighbors(X)

In [23]:
import prince

In [24]:
# We want to reduce the number of features but limit the difference in nearest neighbours
# We stop once only 10% of the sets have no overlap
l = [0]
n = 4
while True:
    n+=1
    mca = prince.MCA(n_components=n)
    mca = mca.fit(X)
    mca = mca.transform(X)
    nbrs = NearestNeighbors(n_neighbors=6, algorithm='ball_tree').fit(mca)
    mca_distances, mca_indices = nbrs.kneighbors(mca)
    l = []
    for i in range(len(indices)):
        l.append(len(set(indices[i][1:]) & set(mca_indices[i][1:])))
    if l.count(0) < len(l)/10:
        break
print(n)

20


In [25]:
mca = prince.MCA(n_components=n)
mca = mca.fit(X)
mca = mca.transform(X)
mca

0         1         2         3         4         5         6   \
0    -0.025074  0.318228  0.047341  0.123570  0.224134 -0.073037 -0.137453   
1    -0.021282  0.241927 -0.002136 -0.087406  0.057331  0.019256 -0.087874   
2    -0.023370 -0.031865  0.161014 -0.097921 -0.095761  0.092606 -0.029033   
3    -0.026508 -0.088908 -0.047582 -0.105501 -0.107253 -0.014130 -0.076722   
4    -0.012232  0.137956  0.082171  0.214607  0.128401  0.168808 -0.021614   
...        ...       ...       ...       ...       ...       ...       ...   
2277 -0.035554 -0.028238 -0.215958 -0.107268  0.085084  0.165797  0.070558   
2278 -0.029716 -0.125359 -0.049122 -0.087392 -0.142736  0.106245  0.070982   
2279 -0.032637 -0.114409 -0.031698  0.096874 -0.044234 -0.132987 -0.083686   
2280 -0.029880  0.020770 -0.158768  0.072235  0.176584 -0.140756 -0.062828   
2281 -0.021416  0.255331 -0.004244 -0.081082  0.047578 -0.073518  0.080293   

            7         8         9         10        11        12        13  \
0     0.100727 -0.154280  0.011982  0.082122 -0.159178  0.054989  0.100243   
1     0.129129 -0.052712  0.005748  0.049175 -0.081430  0.054709  0.069681   
2     0.116824  0.046807 -0.205094  0.035971 -0.067455 -0.058256 -0.050586   
3    -0.052738 -0.013822  0.045562  0.082179  0.056726 -0.056475 -0.011281   
4    -0.127137 -0.045679 -0.059756 -0.028728 -0.000016 -0.064650 -0.023361   
...        ...       ...       ...       ...       ...       ...       ...   
2277  0.010053 -0.008375 -0.034443  0.158405 -0.009923  0.138109 -0.063051   
2278  0.044178 -0.137400  0.119200 -0.104368 -0.190322  0.044277  0.002513   
2279 -0.056408  0.000128  0.088079  0.084779  0.046687 -0.049798  0.029143   
2280 -0.058448 -0.044809 -0.034316  0.003086  0.063460 -0.018722 -0.059429   
2281  0.084510 -0.122858 -0.035789 -0.021306 -0.009319 -0.095536  0.013061   

            14        15        16        17        18        19  
0     0.130588  0.074400 -0.056135  0.024077  0.005094  0.022137  
1    -0.029123  0.076345 -0.049477 -0.045160 -0.061674 -0.007585  
2     0.068098 -0.110289 -0.086624  0.063913  0.039437 -0.066073  
3     0.023507  0.011586  0.008778 -0.022237  0.008995  0.001811  
4    -0.032769 -0.095690  0.013135 -0.096007 -0.121545 -0.037522  
...        ...       ...       ...       ...       ...       ...  
2277 -0.109697 -0.015783  0.022026  0.058317 -0.060263 -0.048436  
2278 -0.090188 -0.094217 -0.101960  0.005031 -0.034131 -0.089062  
2279  0.004833 -0.002069 -0.005928 -0.055002  0.017637  0.058614  
2280 -0.000542  0.107133 -0.107270  0.071350 -0.079835 -0.046602  
2281 -0.073214  0.065775  0.098093  0.081915  0.028091 -0.030774  

[2282 rows x 20 columns]

In [26]:
df["recommendations"] = [i[1:] for i in mca_indices]
df["string_recommendation"] = [[df["name"][j] for j in i[1:]] for i in mca_indices]
for i in df["string_recommendation"][0:3]:
    print(i)

['D31 The New Life', 'Indonesia Sumatra Gayo Espresso', 'Zoom Espresso', 'Ethiopia Guji Uraga More Floral Kudume Washed', 'Kenya AA Ares Phoenix Special']
['Flight Seasonal Espresso', 'Ethiopia Gotiti Natural', 'Mama Cata Mokkita', 'Zoom Espresso', 'Chasing Horizon Natural Espresso']
['Estelí Nicaragua', 'Ethiopia Natural Guji Blue-Donkey 2020', 'Crescent Blend', 'Gigesa Ethiopia', 'Yemen Mocha Haimi']


In [27]:
df.rename(columns={"desc_1":"description"},inplace=True)

In [28]:
df.head(3)

slug  \
0  https://www.coffeereview.com/review/sweety-esp...   
1  https://www.coffeereview.com/review/flora-blen...   
2  https://www.coffeereview.com/review/ethiopia-s...   

                                            all_text  rating       roaster  \
0   \r\n\r\n\r\n95\r\n\r\n\r\nA.R.C.\r\n“Sweety” ...      95        A.R.C.   
1   \r\n\r\n\r\n94\r\n\r\n\r\nA.R.C.\r\nFlora Ble...      94        A.R.C.   
2   \r\n\r\n\r\n92\r\n\r\n\r\nRevel Coffee\r\nEth...      92  Revel Coffee   

                       name           location                        origin  \
0   “Sweety” Espresso Blend   Hong Kong, China              Panama; Ethiopia   
1      Flora Blend Espresso   Hong Kong, China          Africa; Asia Pacific   
2  Ethiopia Shakiso Mormora  Billings, Montana  Guji Zone, southern Ethiopia   

          roast           est_price    review_date  ... flavor  aftertaste  \
0  Medium-Light  HKD $250/227 grams  November 2017  ...    9.0         9.0   
1  Medium-Light  HKD $158/227 grams  November 2017  ...    9.0         8.0   
2  Medium-Light    $16.00/12 ounces  November 2017  ...    9.0         8.0   

   with_milk                                        description  \
0        9.0  Evaluated as espresso. Sweet-toned, deeply ric...   
1        9.0  Evaluated as espresso. Sweetly tart, floral-to...   
2        NaN  Crisply sweet, cocoa-toned. Lemon blossom, roa...   

                                              desc_2  \
0  An espresso blend comprised of coffees from Pa...   
1  An espresso blend comprised of coffees from Af...   
2  This coffee tied for the third-highest rating ...   

                                              desc_3  \
0  A radiant espresso blend that shines equally i...   
1  A floral-driven straight shot, amplified with ...   
2  A gently spice-toned, floral- driven wet-proce...   

                                     characteristics  \
0  [espresso, sweet, rich, chocolati, vanilla, ch...   
1  [espresso, floral, honeysuckl, oak, chocol, th...   
2  [crispli, cocoa, blossom, date, rice, pepperco...   

                                  coffee                recommendations  \
0         “Sweety” Espresso Blend-A.R.C.    [635, 657, 809, 2189, 1127]   
1            Flora Blend Espresso-A.R.C.   [1354, 266, 1740, 809, 2037]   
2  Ethiopia Shakiso Mormora-Revel Coffee  [992, 1148, 1031, 1576, 1502]   

                               string_recommendation  
0  [D31 The New Life, Indonesia Sumatra Gayo Espr...  
1  [Flight Seasonal Espresso, Ethiopia Gotiti Nat...  
2  [Estelí Nicaragua, Ethiopia Natural Guji Blue-...  

[3 rows x 24 columns]

In [29]:
import pickle
with open("data.p","wb") as f:
    pickle.dump(df,f)

In [30]:
data_dict = df.to_dict("index")
import pickle
with open("data.p","wb") as f:
    pickle.dump(data_dict,f)

In [31]:
data_dict

{0: {'slug': 'https://www.coffeereview.com/review/sweety-espresso-blend/',
  'all_text': ' \r\n\r\n\r\n95\r\n\r\n\r\nA.R.C.\r\n“Sweety” Espresso Blend\r\n\r\n\r\n\r\n\r\n\r\n\r\n\r\n\r\nRoaster Location:\r\nHong Kong, China\r\n\r\n\r\nCoffee Origin:\r\nPanama; Ethiopia\r\n\r\n\r\nRoast Level:\r\nMedium-Light\r\n\r\n\r\nAgtron:\r\n50/73\r\n\r\n\r\nEst. Price:\r\nHKD $250/227 grams\r\n\r\n\r\n\r\n\r\n\r\n\r\nReview Date:\r\nNovember 2017\r\n\r\n\r\nAroma:\r\n9\r\n\r\n\r\nBody:\r\n9\t\t\t\t\t\t\t\r\n\r\nFlavor:\r\n9\r\n\r\n\r\nAftertaste:\r\n9\r\n\r\n\r\nWith Milk:\r\n9\r\n\r\n\r\n\r\n\r\nBlind Assessment: Evaluated as espresso. Sweet-toned, deeply rich, chocolaty. Vanilla paste, dark chocolate, narcissus, pink grapefruit zest, black cherry in aroma and cup. Plush, syrupy mouthfeel; resonant, flavor-saturated finish. In three parts milk, rich chocolate tones intensify, along with intimations of vanilla paste and black cherry in the short finish and floral-toned citrus zest in the long. \r

In [33]:
for i in df["roaster"]:
    print(i)

A.R.C.
A.R.C.
Revel Coffee
Roast House
Big Creek Coffee Roasters
Red Rooster Coffee Roaster
Willoughby's Coffee & Tea
Black Oak Coffee Roasters
Wonderstate Coffee
Reunion Island Coffee
PT's Coffee Roasting
Kakalove Cafe
Level Ground Trading
Old Soul Co.
A.R.C.
A.R.C.
A.R.C.
A.R.C.
A.R.C.
A.R.C.
A.R.C.
A.R.C.
Bootstrap Coffee Roasters
Paradise Roasters
Glory Brew
Hula Daddy Kona Coffee
Kakalove Cafe
Jackrabbit Java
Kakalove Cafe
Propeller Coffee
Propeller Coffee
Propeller Coffee
Chocolate Fish Coffee Roasters
Caffe Luxxe
Espresso Republic
Lexington Coffee Roasters
Big Creek Coffee Roasters
Mystic Monk Coffee
Mystic Monk Coffee
Noble Coffee Roasting
Red E Café
Ben's Beans
Espresso Republic
Cimarron Coffee Roasters
Roast House
Red Rooster Coffee Roaster
Speckled Ax
Fumi Coffee
Good Folks Coffee
Flight Coffee Co.
Dragonfly Coffee Roasters
OQ Coffee Co.
Green Stone Coffee
Willoughby's Coffee & Tea
Bird Rock Coffee Roasters
Equator Coffees & Teas
JBC Coffee Roasters
Willoughby's Coffee & Tea